# Import libraries

In [1]:
import pandas as pd
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import re
import time
import datetime
import smtplib
import json
import time    # to be used in loop iterations
import plotly.express as px
from scipy import stats

from sklearn.model_selection import train_test_split, RandomizedSearchCV, cross_val_score
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.feature_selection import SelectFromModel
from scipy.stats import randint
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestRegressor

from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.metrics import mean_squared_error, r2_score
import numpy as np

# Data Loading

In [2]:
# Defining dataframe
df = pd.read_csv(r"C:\Users\chunt\OneDrive\Documents\[01] Data Science\[02]_Projects\[01] Machine Learning\[05] Rent Estimator\mudah-apartment-kl-selangor.csv")

# Data Exploration and Cleaning

## Dropping unused columns

In [3]:
#dropping unused columns
df = df.drop(columns=[
    'completion_year',
    'prop_name', 
    'facilities', 
    'additional_facilities'
])
df

monthly_rent              location property_type rooms  parking  \
0                80        Kota Damansara     Apartment     1      6.0   
1                85        Seri Kembangan          Soho   NaN      1.0   
2               100               Setapak   Condominium     4      2.0   
3               100               Setapak   Condominium     1      NaN   
4               100  Bandar Sri Damansara     Apartment     1      NaN   
...             ...                   ...           ...   ...      ...   
19854         16000                  KLCC   Condominium     4      2.0   
19855         16800                  KLCC   Condominium     4      2.0   
19856         16800                  KLCC   Condominium     3      2.0   
19857         17000                  KLCC   Condominium     7      4.0   
19858         18500          Ampang Hilir   Condominium     4      3.0   

       bathroom  size            furnished        region  
0           1.0   400      Fully Furnished      Selangor  
1           NaN   761                  NaN      Selangor  
2           2.0  1500      Fully Furnished  Kuala Lumpur  
3           1.0   500        Not Furnished  Kuala Lumpur  
4           1.0   400      Fully Furnished      Selangor  
...         ...   ...                  ...           ...  
19854       2.0  3218      Fully Furnished  Kuala Lumpur  
19855       4.0  2195      Fully Furnished  Kuala Lumpur  
19856       5.0  2197      Fully Furnished  Kuala Lumpur  
19857       7.0  7800      Fully Furnished  Kuala Lumpur  
19858       6.0  7506  Partially Furnished  Kuala Lumpur  

[19859 rows x 9 columns]

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19859 entries, 0 to 19858
Data columns (total 9 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   monthly_rent   19859 non-null  int64  
 1   location       19859 non-null  object 
 2   property_type  19859 non-null  object 
 3   rooms          19856 non-null  object 
 4   parking        14224 non-null  float64
 5   bathroom       19856 non-null  float64
 6   size           19859 non-null  int64  
 7   furnished      19857 non-null  object 
 8   region         19859 non-null  object 
dtypes: float64(2), int64(2), object(5)
memory usage: 1.4+ MB


In [5]:
#converting rooms from object to int64
df['rooms'] = pd.to_numeric(df['rooms'], downcast='integer', errors='coerce')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19859 entries, 0 to 19858
Data columns (total 9 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   monthly_rent   19859 non-null  int64  
 1   location       19859 non-null  object 
 2   property_type  19859 non-null  object 
 3   rooms          19854 non-null  float64
 4   parking        14224 non-null  float64
 5   bathroom       19856 non-null  float64
 6   size           19859 non-null  int64  
 7   furnished      19857 non-null  object 
 8   region         19859 non-null  object 
dtypes: float64(3), int64(2), object(4)
memory usage: 1.4+ MB


In [6]:
# Remove rows where 'rooms', 'bathroom', or 'furnished' have NaN values
df = df.dropna(subset=["rooms", "bathroom", "furnished"])

# Replace NaN values in 'parking' column with the mean of 'parking'
df['parking'] = df['parking'].fillna(df['parking'].mean())

# Display information about the DataFrame
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 19854 entries, 0 to 19858
Data columns (total 9 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   monthly_rent   19854 non-null  int64  
 1   location       19854 non-null  object 
 2   property_type  19854 non-null  object 
 3   rooms          19854 non-null  float64
 4   parking        19854 non-null  float64
 5   bathroom       19854 non-null  float64
 6   size           19854 non-null  int64  
 7   furnished      19854 non-null  object 
 8   region         19854 non-null  object 
dtypes: float64(3), int64(2), object(4)
memory usage: 1.5+ MB


C:\Users\chunt\AppData\Local\Temp\ipykernel_8876\303082220.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['parking'] = df['parking'].fillna(df['parking'].mean())


## Detecing and Cleaning Outliers (monthly_rent)

In [7]:
import plotly.graph_objects as go

# Create a boxplot using plotly.graph_objects
fig = go.Figure()

# Add boxplot trace
fig.add_trace(go.Box(
    y=df['monthly_rent'],
    name='Monthly Rent' # Optional: Display the mean and standard deviation
))

# Update layout
fig.update_layout(
    title='Boxplot of Monthly Rent',
    yaxis_title='Monthly Rent (RM)'
)


# Show the plot
fig.show()

In [8]:
# Define a function to calculate Z-scores and remove outliers for multiple columns
def remove_outliers(df, column, threshold=3.5):
    # Calculate Z-scores for the specified column
    df['z_score'] = stats.zscore(df['monthly_rent'])
    
    # Mark rows as 'Outlier' or 'Not Outlier' based on the threshold
    df['outlier'] = df['z_score'].apply(lambda x: 'Outlier' if abs(x) > threshold else 'Not Outlier')
    
    # Filter rows where the specified column is not an outlier
    df_cleaned = df[df['outlier'] == 'Not Outlier']
    
    return df_cleaned

# Apply the function to remove outliers for the relevant columns
df_cleaned = remove_outliers(df, ['monthly_rent'])

df_cleaned = remove_outliers(df, ['monthly_rent'])
fig = px.box(df_cleaned, y=['monthly_rent','rooms', 'parking', 'bathroom', 'size'])

# Show the plot
fig.show()


C:\Users\chunt\AppData\Local\Temp\ipykernel_8876\3533663965.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\chunt\AppData\Local\Temp\ipykernel_8876\3533663965.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\chunt\AppData\Local\Temp\ipykernel_8876\3533663965.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-d

In [9]:
# def filter_large_rows(df_cleaned, size_column, min_size=10000):
#     # Filter rows where the size column is greater than the minimum size
#     df_cleaned = df_cleaned[df_cleaned[size_column] > min_size]
    
#     return df_cleaned
# df_cleaned = filter_large_rows(df, 'size')
# print(df_cleaned)

In [10]:
# Remove rows where 'size' is greater than 10,000
df_cleaned = df_cleaned[df_cleaned['size'] <= 5000]

In [11]:
fig = px.box(df_cleaned, y=['monthly_rent','rooms', 'parking', 'bathroom', 'size'])

# Show the plot
fig.show()

In [12]:
print(df_cleaned.shape)

(19680, 11)


## Finding the distributions of furnished vs partially furnished vs unfurnished

In [13]:
# Create the box plot
fig = px.box(df_cleaned, x='furnished', y='monthly_rent', title="Rent vs Furnishing Type",
             labels={'furnished': 'Furnishing Type', 'rent': 'Rent (in MYR)'})


# Update hover information to show furnishing type and rent for each point
fig.update_traces(hovertemplate='Furnishing: %{x}<br>Rent: %{y} MYR')

# Show the plot
fig.show()

In [14]:
df_cleaned = df_cleaned[df['monthly_rent'] >= 500]

C:\Users\chunt\AppData\Local\Temp\ipykernel_8876\387630199.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



In [15]:
print(df_cleaned.shape)

(19588, 11)


In [16]:
df_cleaned['location'].unique()

array(['Cheras', 'Petaling Jaya', 'Puncak Alam', 'Bandar Sunway',
       'Kajang', 'Kota Damansara', 'Seri Kembangan', 'Damansara Damai',
       'Bandar Sri Damansara', 'Damansara Perdana', 'Batu Caves',
       'Puchong', 'Shah Alam', 'Rawang', 'Kuala Selangor', 'Semenyih',
       'Sepang', 'Cyberjaya', 'Klang', 'Bukit Jalil', 'Setapak', 'OUG',
       'Desa Petaling', 'Kepong', 'Beranang', 'Bandar Saujana Putra',
       'Kuala Langat', 'Bandar Sungai Long', 'Setia Alam', '360',
       'Serendah', 'Bangi', 'Wangsa Maju', 'Titiwangsa', 'Kuchai Lama',
       'Sungai Besi', 'Mid Valley City', 'Serdang', 'Ampang', 'Selayang',
       'Dengkil', 'Gombak', 'Balakong', 'Port Klang', 'Bukit Subang',
       'Banting', 'Kapar', 'Pandan Indah', 'Jenjarom', 'Keramat',
       'Old Klang Road', 'Salak Selatan', 'Sri Damansara', 'Sungai Buloh',
       'Hulu Langat', 'Putra Heights', 'Puchong South', 'Sentul',
       'Jalan Kuching', 'Pandan Jaya', 'Jalan Ipoh',
       'Bandar Tasik Selatan', 'Ampang Hi

In [17]:
df_cleaned['property_type'].unique()


array(['Condominium', 'Flat', 'Apartment', 'Service Residence', 'Others',
       'Townhouse Condo', 'Studio', 'Duplex'], dtype=object)

In [18]:
df_cleaned['furnished'].unique()

array(['Fully Furnished', 'Not Furnished', 'Partially Furnished'],
      dtype=object)

In [19]:
df_cleaned['region'].unique()

array(['Kuala Lumpur', 'Selangor'], dtype=object)

In [20]:
print(df_cleaned.shape)
df

(19588, 11)


monthly_rent              location property_type  rooms   parking  \
0                80        Kota Damansara     Apartment    1.0  6.000000   
2               100               Setapak   Condominium    4.0  2.000000   
3               100               Setapak   Condominium    1.0  1.416948   
4               100  Bandar Sri Damansara     Apartment    1.0  1.416948   
5               100             Shah Alam   Condominium    3.0  1.000000   
...             ...                   ...           ...    ...       ...   
19854         16000                  KLCC   Condominium    4.0  2.000000   
19855         16800                  KLCC   Condominium    4.0  2.000000   
19856         16800                  KLCC   Condominium    3.0  2.000000   
19857         17000                  KLCC   Condominium    7.0  4.000000   
19858         18500          Ampang Hilir   Condominium    4.0  3.000000   

       bathroom  size            furnished        region    z_score  \
0           1.0   400      Fully Furnished      Selangor  -1.631289   
2           2.0  1500      Fully Furnished  Kuala Lumpur  -1.610018   
3           1.0   500        Not Furnished  Kuala Lumpur  -1.610018   
4           1.0   400      Fully Furnished      Selangor  -1.610018   
5           3.0  1000        Not Furnished      Selangor  -1.610018   
...         ...   ...                  ...           ...        ...   
19854       2.0  3218      Fully Furnished  Kuala Lumpur  15.300571   
19855       4.0  2195      Fully Furnished  Kuala Lumpur  16.151419   
19856       5.0  2197      Fully Furnished  Kuala Lumpur  16.151419   
19857       7.0  7800      Fully Furnished  Kuala Lumpur  16.364131   
19858       6.0  7506  Partially Furnished  Kuala Lumpur  17.959469   

           outlier  
0      Not Outlier  
2      Not Outlier  
3      Not Outlier  
4      Not Outlier  
5      Not Outlier  
...            ...  
19854      Outlier  
19855      Outlier  
19856      Outlier  
19857      Outlier  
19858      Outlier  

[19854 rows x 11 columns]

In [21]:
print(df_cleaned.columns)

Index(['monthly_rent', 'location', 'property_type', 'rooms', 'parking',
       'bathroom', 'size', 'furnished', 'region', 'z_score', 'outlier'],
      dtype='object')


In [22]:
#dropping unused columns
df_cleaned = df_cleaned.drop(columns=[
    'outlier', 'z_score'
])
df_cleaned

monthly_rent       location property_type  rooms   parking  bathroom  \
93              500         Cheras   Condominium    5.0  1.416948       4.0   
94              500         Cheras          Flat    2.0  1.416948       1.0   
95              500         Cheras          Flat    1.0  1.416948       1.0   
96              500  Petaling Jaya     Apartment    3.0  1.000000       2.0   
97              500    Puncak Alam          Flat    3.0  1.416948       2.0   
...             ...            ...           ...    ...       ...       ...   
19685          4899           KLCC   Condominium    2.0  2.000000       2.0   
19686          4900     Mont Kiara   Condominium    3.0  2.000000       3.0   
19687          4900  Bukit Bintang   Condominium    2.0  1.000000       2.0   
19688          4900           KLCC   Condominium    3.0  2.000000       3.0   
19689          4900           KLCC   Condominium    2.0  2.000000       2.0   

       size            furnished        region  
93      910      Fully Furnished  Kuala Lumpur  
94      650        Not Furnished  Kuala Lumpur  
95      550      Fully Furnished  Kuala Lumpur  
96      650        Not Furnished      Selangor  
97      655        Not Furnished      Selangor  
...     ...                  ...           ...  
19685  1485      Fully Furnished  Kuala Lumpur  
19686  1907      Fully Furnished  Kuala Lumpur  
19687  1098      Fully Furnished  Kuala Lumpur  
19688  1600  Partially Furnished  Kuala Lumpur  
19689  1500      Fully Furnished  Kuala Lumpur  

[19588 rows x 9 columns]

## Converting categorical variables to numerical values

In [23]:
# Initialize the LabelEncoder
label_encoder = LabelEncoder()

# Apply Label Encoding to each categorical variable

# Creating a custom mapping for the location values
location_mapping = {
    'Taman Desa': 0, 'Cheras': 1, 'Sentul': 2, 'Mont Kiara': 3, 'Setapak': 4, 'Ampang': 5, 'Segambut': 6,
    'Desa ParkCity': 7, 'Bukit Jalil': 8, 'Kepong': 9, 'KL City': 10, 'Wangsa Maju': 11,
    'Solaris Dutamas': 12, 'Jalan Kuching': 13, 'Bandar Menjalara': 14, 'Desa Pandan': 15,
    'Old Klang Road': 16, 'KLCC': 17, 'Ampang Hilir': 18, 'Bukit Bintang': 19, 'Jalan Ipoh': 20,
    'Setiawangsa': 21, 'Gombak': 22, 'Pantai': 23, 'Sungai Besi': 24, 'Jinjang': 25, 'Sri Petaling': 26,
    'Bangsar South': 27, 'Brickfields': 28, 'Kuchai Lama': 29, 'Jalan Sultan Ismail': 30,
    'Bangsar': 31, 'Pandan Indah': 32, 'Pandan Jaya': 33, 'Damansara Heights': 34,
    'Bandar Damai Perdana': 35, 'Titiwangsa': 36, 'Bandar Tasik Selatan': 37,
    'Pandan Perdana': 38, 'Keramat': 39, 'Pudu': 40, 'Sri Damansara': 41, 'OUG': 42,
    'Taman Tun Dr Ismail': 43, 'Sri Hartamas': 44, 'Taman Melawati': 45, 'Desa Petaling': 46,
    'Puchong': 47, 'Seputeh': 48, 'KL Sentral': 49, 'City Centre': 50, 'Bukit Tunku': 51, 'Others': 52,
    'Serdang': 53, 'Mid Valley City': 54, 'Salak Selatan': 55, 'KL Eco City': 56,
    'Sungai Penchala': 57, 'Damansara': 58, 'Chan Sow Lin': 59, 'Cyberjaya': 60, 'Shah Alam': 61,
    'Klang': 62, 'Petaling Jaya': 63, '389': 64, 'Subang Jaya': 65, 'Bandar Sunway': 66,
    'Seri Kembangan': 67, 'Kajang': 68, 'Rawang': 69, 'Kota Damansara': 70, 'Batu Caves': 71,
    'Semenyih': 72, 'Bukit Jelutong': 73, 'USJ': 74, 'Damansara Damai': 75,
    'Bandar Mahkota Cheras': 76, 'Puncak Alam': 77, 'Sepang': 78, 'Kuala Langat': 79,
    'Setia Alam': 80, 'Selayang': 81, 'Sungai Buloh': 82, 'Bangi': 83, 'Dengkil': 84,
    'Ara Damansara': 85, 'I-City': 86, 'Bandar Sri Damansara': 87, 'Damansara Perdana': 88,
    'Bandar Saujana Putra': 89, 'Kota Kemuning': 90, 'Ulu Klang': 91, '360': 92, 'Kapar': 93,
    'Balakong': 94, 'Bandar Sungai Long': 95, 'Port Klang': 96, 'Hulu Langat': 97,
    'Bandar Kinrara': 98, 'Jenjarom': 99, 'Glenmarie': 100, 'Kelana Jaya': 101, 'Beranang': 102,
    'Puchong South': 103, 'Alam Impian': 104, 'Pulau Indah (Pulau Lumut)': 105, '639': 106,
    'Bandar Bukit Tinggi': 107, 'Putra Heights': 108, 'Saujana Utama': 109, 'Bandar Bukit Raja': 110,
    '43': 111, 'Subang Bestari': 112, 'Bandar Utama': 113, '369': 114, 'Bandar Botanic': 115,
    'Banting': 116, 'Kuala Selangor': 117, 'Salak Tinggi': 118, 'Serendah': 119, 'Bukit Beruntung': 120,
    'Mutiara Damansara': 121, 'Damansara Jaya': 122, '517': 123, 'Telok Panglima Garang': 124,
    'Bukit Subang': 125, 'Puncak Jalil': 126
}

# Applying the mapping to your dataframe
df_cleaned['location'] = df_cleaned['location'].map(location_mapping)


# Creating a custom mapping for property types
property_type_mapping = {
    'Condominium': 0,
    'Apartment': 1,
    'Service Residence': 2,
    'Studio': 3,
    'Flat': 4,
    'Duplex': 5,
    'Others': 6,
    'Townhouse Condo': 7,
    'Condo / Services residence / Penthouse / Townhouse': 8,
    'Houses': 9
}

# Applying the mapping to your dataframe
df_cleaned['property_type'] = df_cleaned['property_type'].map(property_type_mapping)

# Manual mapping for encoding
furnished_mapping = {
    'Not Furnished':0,
    'Partially Furnished':1,
    'Fully Furnished':2
}
region_mapping = {
    'Kuala Lumpur':0,
    'Selangor':1
}

df_cleaned['furnished'] = df_cleaned['furnished'].map(furnished_mapping)
df_cleaned['region'] = df_cleaned['region'].map(region_mapping)
# mappings = {
#     'furnished' : {'Not Furnished':0,'Partially Furnished':1,'Fully Furnished':2},
#     'region' : {'Kuala Lumpur':0,'Selangor':1}
# }

# for col, mapping in mappings.items():
#     df[col] = df[col].map(mapping)

# Print unique values in the specified column for both DataFrames
column_name = 'education_level'  # Replace with the actual column name


df_cleaned

monthly_rent  location  property_type  rooms   parking  bathroom  size  \
93              500         1              0    5.0  1.416948       4.0   910   
94              500         1              4    2.0  1.416948       1.0   650   
95              500         1              4    1.0  1.416948       1.0   550   
96              500        63              1    3.0  1.000000       2.0   650   
97              500        77              4    3.0  1.416948       2.0   655   
...             ...       ...            ...    ...       ...       ...   ...   
19685          4899        17              0    2.0  2.000000       2.0  1485   
19686          4900         3              0    3.0  2.000000       3.0  1907   
19687          4900        19              0    2.0  1.000000       2.0  1098   
19688          4900        17              0    3.0  2.000000       3.0  1600   
19689          4900        17              0    2.0  2.000000       2.0  1500   

       furnished  region  
93             2       0  
94             0       0  
95             2       0  
96             0       1  
97             0       1  
...          ...     ...  
19685          2       0  
19686          2       0  
19687          2       0  
19688          1       0  
19689          2       0  

[19588 rows x 9 columns]

In [24]:
print(df_cleaned.shape)

(19588, 9)


# Prepare dataset for modelling

## Data Splitting

In [25]:
# Define features (X) and target (y)
X = df_cleaned.drop(columns=['monthly_rent'])
y = df_cleaned['monthly_rent']

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)



## Creating model for RandomForestRegressor, LinearRegression, GradientBoostingRegressor

In [26]:
# Define RandomForestRegressor model
rfr_model = RandomForestRegressor(
    random_state=42
)

# Define LinearRegression model
lr_model = LinearRegression()

# Define GradientBoostingRegressor model
gbr_model = GradientBoostingRegressor(
    # n_estimators=52,
    # learning_rate=0.01,
    # max_depth=13,
    # min_samples_split=10,
    # min_samples_leaf=13,
    random_state=42
)

In [27]:
# from sklearn.model_selection import GridSearchCV
# from sklearn.ensemble import RandomForestRegressor

# # Define the model
# rf = RandomForestRegressor()

# # Define the parameter grid to search over
# param_grid = {
#     'n_estimators': [50, 100, 200],
#     'max_depth': [10, 20, 30, None],
#     'min_samples_split': [2, 5, 10],
#     'min_samples_leaf': [1, 2, 4],
#     'bootstrap': [True, False]
# }

# # Set up the grid search with 5-fold cross-validation
# grid_search = GridSearchCV(estimator=rf, param_grid=param_grid, cv=5, scoring='neg_mean_squared_error', verbose=2, n_jobs=-1)

# # Fit the model
# grid_search.fit(X_train, y_train)

# # Best parameters and corresponding score
# print(f"Best Parameters: {grid_search.best_params_}")
# print(f"Best RMSE: {np.sqrt(-grid_search.best_score_)}")


## Training models, making predictions and evaluating models

In [28]:
# Train the model
rfr_model.fit(X_train, y_train)
lr_model.fit(X_train, y_train)
gbr_model.fit(X_train, y_train)

# Make predictions
y_pred = rfr_model.predict(X_test)
y_pred2 = lr_model.predict(X_test)
y_pred3 = gbr_model.predict(X_test)

# Evaluate the model
rmse = np.sqrt(mean_squared_error(y_test, y_pred))
r2 = r2_score(y_test, y_pred)
rmse2 = np.sqrt(mean_squared_error(y_test, y_pred2))
r22 = r2_score(y_test, y_pred2)
rmse3 = np.sqrt(mean_squared_error(y_test, y_pred3))
r23 = r2_score(y_test, y_pred3)

# Print the evaluation metrics
print(f"RandomForestRegressor: RMSE = {rmse}, R² = {r2}")
print(f"LinearRegression: RMSE = {rmse2}, R² = {r22}")
print(f"GradientBoostingRegressor: RMSE = {rmse3}, R² = {r23}")

RandomForestRegressor: RMSE = 327.43497436321456, R² = 0.77707305937508
LinearRegression: RMSE = 490.6678950172265, R² = 0.49940361493536023
GradientBoostingRegressor: RMSE = 407.09614486579545, R² = 0.6554070376915744


In [29]:
import joblib

# Save the model to a file
joblib.dump(rfr_model, 'randomregressor_rent.pkl')

['randomregressor_rent.pkl']

# Saving the model

In [31]:
# Load the model
randomregressor = joblib.load('randomregressor_rent.pkl')

# Check if the model has the 'feature_names_in_' attribute
if hasattr(randomregressor, 'feature_names_in_'):
    print("Model features:", randomregressor.feature_names_in_)
else:
    print("Feature names not available. Check the model training script.")

Model features: ['location' 'property_type' 'rooms' 'parking' 'bathroom' 'size'
 'furnished' 'region']


# Feature Importance

In [32]:
importance = rfr_model.feature_importances_

# Create a DataFrame to store feature names and their importance scores
feature_names = X_train.columns  # Assuming you are using the original X_train for column names
feature_importance_df = pd.DataFrame({
    'Feature': feature_names,
    'Importance': importance
})

# Sort the DataFrame by importance
feature_importance_df.sort_values(by='Importance', ascending=False, inplace=True)

# Print feature importances
print("Feature importances:")
for i, row in feature_importance_df.iterrows():
    print(f'Feature: {row["Feature"]}, Score: {row["Importance"]:.4f}')

Feature importances:
Feature: size, Score: 0.3561
Feature: furnished, Score: 0.2442
Feature: location, Score: 0.1779
Feature: property_type, Score: 0.0561
Feature: region, Score: 0.0503
Feature: parking, Score: 0.0462
Feature: rooms, Score: 0.0432
Feature: bathroom, Score: 0.0259
